## Analyze your relation file

In this jupyter notebook, we will build a graph based on your relation file and do some analysis on it. Such as the number of nodes, the number of edges, the number of subgraphs, and so on. Based on the metrics, you can know whether your relation file is valid for training or not. If your relation file have too many subgraphs and no any subgraph is large enough (e.g. the percent of the number of nodes and edges in a subgraph is no more than 90% of the total number of nodes and edges in the graph.), you may need to consider to add more relations to your relation file.

In our opinion, the number of subgraphs should be as small as possible, and the number of nodes and edges in a subgraph should be as large as possible. In this way, the model can learn more information from the graph.

## Prepare your relation file

Prepare your relation file and specify the path in the following cell. The relation file should be a csv/tsv file and the first line should be the header. For the format of the entity & relation file, please refer to the [README](../graph_data/README.md). If you want to build your own entity & relation file, please refer to the [KG README](../graph_data/KG_README.md) for more details.

We assume that the relation file is named as `knowledge_graph.tsv`, the entity file is named as `annotated_entities.tsv`, and are located in the `datasets` directory or `you can specify the path in the following cell`.

In [45]:
import os

# datadir = os.path.join(os.path.dirname(os.getcwd()), "datasets", "biomedgps-v2")
datadir = "/var/folders/4s/d4nr1sg91ps1k3qz00h28w_r0000gp/T/tmpregc5oy4/"
graph_data_dir = os.path.join(os.path.dirname(os.getcwd()), "graph_data")

In [80]:
# relation_file = os.path.join(datadir, "knowledge_graph.tsv")
relation_file = os.path.join(
    datadir, "knowledge_graph_ignore_relation_types_filtered.tsv"
)
# entities_file = os.path.join(datadir, "annotated_entities.tsv")
entities_file = os.path.join(graph_data_dir, "entities.tsv")

if not os.path.exists(relation_file):
    raise FileNotFoundError("Relation file not found: {}".format(relation_file))

if not os.path.exists(entities_file):
    raise FileNotFoundError("Entity file not found: {}".format(entities_file))

## Dependencies

We defined all related functions in `lib/graph.py` module. Before doing the graph analysis, we need to import the module. In addition, we assume that you have followed the instructions in the [README](../README.md) file and have installed all the required dependencies.

In [7]:
import os
import sys

libdir = os.path.join(os.path.dirname(os.getcwd()), "lib")
sys.path.append(libdir)

from graph import (
    get_num_nodes,
    get_num_edges,
    get_num_subgraphs,
    create_graph,
    get_subgraph,
)

## Build a undirected graph from the data

In [8]:
G = create_graph(
    relation_file,
    entity_file=entities_file,
    directed=False,
    allow_multiple_edges=True,
)
directed_G = create_graph(
    relation_file, entity_file=entities_file, directed=True, allow_multiple_edges=True
)

### How many nodes, edges, and subgraphs are there in the graph?

In [9]:
get_num_nodes(G), get_num_edges(G), get_num_subgraphs(G)

(99372, 15070186, 54)

In [10]:
get_num_nodes(directed_G), get_num_edges(directed_G), get_num_subgraphs(directed_G)

(99372, 15070186, 54)

### How many nodes and edges are related to a subgraph which starts with our target node?

In [11]:
# We assume that our target node is ME/CFS, the node id is MONDO:0005404 (see entities.tsv) and the node type is Disease.
disease = ("MONDO:0005404", "Disease")

subgraph = get_subgraph(G, start_node=disease)

get_num_nodes(subgraph), get_num_edges(subgraph)

(99264, 15070082)

### Distribution of Relationship Types in the Graph

In [81]:
from collections import Counter
import pandas as pd
import plotly.express as px

knowledge_graph = pd.read_csv(relation_file, sep="\t")
# relation_types = [data["relation"] for u, v, data in G.edges(data = True)]
# formatted_relation_types = [data["formatted_relation"] for u, v, data in G.edges(data = True)]
relation_types = knowledge_graph["relation_type"].values
formatted_relation_types = knowledge_graph["formatted_relation_type"].values
relation_counts = Counter(relation_types)
formatted_relation_counts = Counter(formatted_relation_types)

relation_type_df = pd.DataFrame.from_dict(relation_counts, orient="index").reset_index()
relation_type_df.columns = ["Relationship Type", "Count"]

formatted_relation_type_df = pd.DataFrame.from_dict(
    formatted_relation_counts, orient="index"
).reset_index()
formatted_relation_type_df.columns = ["Formatted Relationship Type", "Count"]

In [82]:
relation_type_df

Relationship Type    Count
0     CTD::decreases^expression::Compound:Gene   583291
1     CTD::increases^expression::Compound:Gene   646612
2      CTD::affects^cotreatment::Compound:Gene   279997
3       CTD::affects^expression::Compound:Gene   131309
4       CTD::decreases^reaction::Compound:Gene   124659
..                                         ...      ...
169      PrimeKG::indication::Compound:Disease    15599
170   PrimeKG::off-label_use::Compound:Disease     4478
171      PrimeKG::interacts_with::Gene:Pathway    42507
172  PrimeKG::expression_present::Gene:Anatomy  1518060
173   PrimeKG::expression_absent::Gene:Anatomy    19884

[174 rows x 2 columns]

In [83]:
formatted_relation_type_df

Formatted Relationship Type   Count
0                     BioMedGPS::E-::Compound:Gene  610862
1                     BioMedGPS::E+::Compound:Gene  690901
2                 BioMedGPS::Target::Gene:Compound  314157
3                      BioMedGPS::E::Compound:Gene  150070
4                BioMedGPS::Blocker::Compound:Gene  179191
..                                             ...     ...
61  BioMedGPS::Interaction::Gene:BiologicalProcess  285352
62  BioMedGPS::Interaction::Gene:CellularComponent  154890
63            BioMedGPS::Interaction::Gene:Pathway   85014
64  BioMedGPS::Interaction::Gene:MolecularFunction  136644
65                     BioMedGPS::NE::Anatomy:Gene   39768

[66 rows x 2 columns]

In [84]:
fig = px.bar(
    relation_type_df.sort_values("Count", ascending=False),
    x="Relationship Type",
    y="Count",
    title="Distribution of Relationship Types in the Graph",
)

fig.show()

In [85]:
fig = px.bar(
    formatted_relation_type_df.sort_values("Count", ascending=False),
    x="Formatted Relationship Type",
    y="Count",
    title="Distribution of Formatted Relationship Types in the Graph",
)

fig.show()

In [86]:
formatted_relation_type_df.sort_values("Count", ascending=False, inplace=True)
formatted_relation_type_df

Formatted Relationship Type    Count
25                     BioMedGPS::E::Anatomy:Gene  3562527
21              BioMedGPS::Interaction::Gene:Gene  1462362
1                    BioMedGPS::E+::Compound:Gene   690901
0                    BioMedGPS::E-::Compound:Gene   610862
48        BioMedGPS::InBP::Gene:BiologicalProcess   541950
..                                            ...      ...
43          BioMedGPS::Interaction::Compound:Gene       96
46         BioMedGPS::CleavageReaction::Gene:Gene       93
47          BioMedGPS::ProteinCleavage::Gene:Gene       67
17             BioMedGPS::Antibody::Compound:Gene       61
44  BioMedGPS::AdpRibosylationReaction::Gene:Gene       58

[66 rows x 2 columns]

In [87]:
formatted_relation_type_df[
    formatted_relation_type_df["Formatted Relationship Type"].str.endswith("Compound:Compound")
].sort_values("Count", ascending=False)

Formatted Relationship Type  Count
19  BioMedGPS::SimilarWith::Compound:Compound   6455

In [88]:
formatted_relation_type_df[
    formatted_relation_type_df["Formatted Relationship Type"].str.contains("Anatomy")
].sort_values("Count", ascending=False)

Formatted Relationship Type    Count
25             BioMedGPS::E::Anatomy:Gene  3562527
26            BioMedGPS::E-::Anatomy:Gene   102240
27            BioMedGPS::E+::Anatomy:Gene    97848
65            BioMedGPS::NE::Anatomy:Gene    39768
57  BioMedGPS::LocatedIn::Disease:Anatomy     3622

In [89]:
formatted_relation_type_df[
    formatted_relation_type_df["Formatted Relationship Type"].str.match(".*?::Gene:(BiologicalProcess|CellularComponent|MolecularFunction|Pathway)")
].sort_values("Count", ascending=False)

Formatted Relationship Type   Count
48         BioMedGPS::InBP::Gene:BiologicalProcess  541950
61  BioMedGPS::Interaction::Gene:BiologicalProcess  285352
62  BioMedGPS::Interaction::Gene:CellularComponent  154890
64  BioMedGPS::Interaction::Gene:MolecularFunction  136644
49         BioMedGPS::InMF::Gene:MolecularFunction   94029
63            BioMedGPS::Interaction::Gene:Pathway   85014
50         BioMedGPS::InCC::Gene:CellularComponent   71563
58              BioMedGPS::InPathway::Gene:Pathway   12587

In [90]:
formatted_relation_type_df[
    formatted_relation_type_df["Formatted Relationship Type"].str.contains("Gene:Gene")
].sort_values("Count", ascending=False)

Formatted Relationship Type    Count
21                BioMedGPS::Interaction::Gene:Gene  1462362
22                 BioMedGPS::Influencer::Gene:Gene   360378
23                     BioMedGPS::Binder::Gene:Gene   322605
29                  BioMedGPS::Activator::Gene:Gene    89006
32                     BioMedGPS::Covary::Gene:Gene    61690
36                  BioMedGPS::Inhibitor::Gene:Gene    28959
38       BioMedGPS::PostTranslationalMod::Gene:Gene    15113
30                          BioMedGPS::E::Gene:Gene    10109
37                         BioMedGPS::E+::Gene:Gene     9880
33                  BioMedGPS::InPathway::Gene:Gene     4108
42                 BioMedGPS::InLocation::Gene:Gene     3468
40                  BioMedGPS::InComplex::Gene:Gene     1863
34    BioMedGPS::PhosphorylationReaction::Gene:Gene     1328
45     BioMedGPS::UbiquitinationReaction::Gene:Gene      371
35  BioMedGPS::DePhosphorylationReaction::Gene:Gene      303
46           BioMedGPS::CleavageReaction::Gene:Gene       93
47            BioMedGPS::ProteinCleavage::Gene:Gene       67
44    BioMedGPS::AdpRibosylationReaction::Gene:Gene       58

In [91]:
formatted_relation_type_df[
    formatted_relation_type_df["Formatted Relationship Type"].str.contains("Disease:Disease")
].sort_values("Count", ascending=False)

Formatted Relationship Type  Count
18  BioMedGPS::SimilarWith::Disease:Disease    686

### Entities in different species

In [93]:
## Number of Mouse / Rat / Human Genes
entities = pd.read_csv(entities_file, sep="\t")
genes = entities[entities["label"] == "Gene"]
mouse_genes = genes[genes["taxid"] == 10090]
rat_genes = genes[genes["taxid"] == 10116]
human_genes = genes[genes["taxid"] == 9606]

print("Number of Entities: ", len(mouse_genes), len(rat_genes), len(human_genes))
knowledge_graph = pd.read_csv(relation_file, sep="\t")
mouse_relations = knowledge_graph[
    knowledge_graph["source_id"].isin(mouse_genes["id"])
    | knowledge_graph["target_id"].isin(mouse_genes["id"])
]

human_relations = knowledge_graph[
    knowledge_graph["source_id"].isin(human_genes["id"])
    | knowledge_graph["target_id"].isin(human_genes["id"])
]

len(mouse_relations), len(human_relations)

/var/folders/4s/d4nr1sg91ps1k3qz00h28w_r0000gp/T/ipykernel_325/1254821760.py:2: DtypeWarning:

Columns (5,6) have mixed types. Specify dtype option on import or set low_memory=False.



Number of Entities:  50015 0 44000


(110419, 9990154)

In [94]:
human_mouse_gene_mappings = pd.read_csv(os.path.join(graph_data_dir, "mapping", "human_mouse_gene_mappings.tsv"), sep="\t")
human_mouse_gene_mappings

key     organism_mouse  taxid_mouse symbol_mouse entrez_id_mouse  \
0      47367020  mouse, laboratory        10090        Banf1    ENTREZ:23825   
1      47367021  mouse, laboratory        10090        Pde9a    ENTREZ:18585   
2      47367022  mouse, laboratory        10090       Asrgl1    ENTREZ:66514   
3      47367023  mouse, laboratory        10090         Clpb    ENTREZ:20480   
4      47367024  mouse, laboratory        10090          Emd    ENTREZ:13726   
...         ...                ...          ...          ...             ...   
24580  47387708  mouse, laboratory        10090       Zswim1    ENTREZ:71971   
24581  47387709  mouse, laboratory        10090       Zswim3    ENTREZ:67538   
24582  47387710  mouse, laboratory        10090       Zswim4   ENTREZ:212168   
24583  47387711  mouse, laboratory        10090       Zswim9   ENTREZ:321008   
24584  47387712  mouse, laboratory        10090        Zwint    ENTREZ:52696   

      mgi_id_mouse  hgnc_id_mouse  omim_gene_id_mouse  location_mouse  \
0      MGI:1346330            NaN                 NaN   Chr19 4.31 cM   
1      MGI:1277179            NaN                 NaN  Chr17 16.23 cM   
2      MGI:1913764            NaN                 NaN   Chr19 6.06 cM   
3      MGI:1100517            NaN                 NaN   Chr7 54.63 cM   
4       MGI:108117            NaN                 NaN   ChrX 37.92 cM   
...            ...            ...                 ...             ...   
24580  MGI:1919221            NaN                 NaN   Chr2 85.27 cM   
24581  MGI:1914788            NaN                 NaN   Chr2 85.27 cM   
24582  MGI:2443726            NaN                 NaN   Chr8 40.59 cM   
24583  MGI:2447816            NaN                 NaN    Chr7 7.82 cM   
24584  MGI:1289227            NaN                 NaN  Chr10 37.15 cM   

          genome_coordinates_mouse  ... symbol_human entrez_id_human  \
0         Chr19:5414661-5416904(-)  ...        BANF1     ENTREZ:8815   
1       Chr17:31605184-31695284(+)  ...        PDE9A     ENTREZ:5152   
2         Chr19:9089083-9112930(-)  ...       ASRGL1    ENTREZ:80150   
3      Chr7:101312958-101444667(+)  ...         CLPB    ENTREZ:81570   
4        ChrX:73298293-73305154(+)  ...          EMD     ENTREZ:2010   
...                            ...  ...          ...             ...   
24580  Chr2:164664933-164668791(+)  ...       ZSWIM1    ENTREZ:90204   
24581  Chr2:164647034-164664047(+)  ...       ZSWIM3   ENTREZ:140831   
24582    Chr8:84937571-84963671(-)  ...       ZSWIM4    ENTREZ:65249   
24583    Chr7:12992894-13012647(-)  ...       ZSWIM9   ENTREZ:374920   
24584   Chr10:72490678-72510796(+)  ...        ZWINT    ENTREZ:11130   

      mgi_id_human hgnc_id_human  omim_gene_id_human       location_human  \
0              NaN    HGNC:17397         OMIM:603811          Chr11 q13.1   
1              NaN     HGNC:8795         OMIM:602973          Chr21 q22.3   
2              NaN    HGNC:16448         OMIM:609212          Chr11 q12.3   
3              NaN    HGNC:30664         OMIM:616254          Chr11 q13.4   
4              NaN     HGNC:3331         OMIM:300384             ChrX q28   
...            ...           ...                 ...                  ...   
24580          NaN    HGNC:16155                 NaN         Chr20 q13.12   
24581          NaN    HGNC:16157         OMIM:620336         Chr20 q13.12   
24582          NaN    HGNC:25704         OMIM:620539  Chr19 p13.13-p13.12   
24583          NaN    HGNC:34495                 NaN         Chr19 q13.33   
24584          NaN    HGNC:13195         OMIM:609177          Chr10 q21.1   

          genome_coordinates_human  \
0       Chr11:66002079-66004149(+)   
1       Chr21:42653621-42775509(+)   
2       Chr11:62337448-62401431(+)   
3       Chr11:72285495-72434680(-)   
4      ChrX:154379273-154381574(+)   
...                            ...   
24580   Chr20:45880920-45885266(+)   
24581   Chr20:45857614-45879122(+)   
24582   Chr19:13795443-13832254(+)   
2458

In [95]:
# NOTE: There might be multiple mappings for a single mouse gene, we will use the first mapping for now. such as PTCD1[ENTREZ:26024] and ATP5MF-PTCD1[ENTREZ:100526740] have the same mouse gene mapping. Ptcd1[ENTREZ: 71799]
human_mouse_gene_map = dict(
    zip(
        human_mouse_gene_mappings["entrez_id_mouse"],
        human_mouse_gene_mappings["entrez_id_human"],
    )
)
human_mouse_gene_map["ENTREZ:71799"]

'ENTREZ:26024'

In [97]:
# We don't like mouse genes, let's convert them to human genes. If a mouse gene doesn't have a human gene mapping, we will keep the mouse gene. So the users can see that the gene is a mouse gene.
# Convert the mouse_genes["id"] Series to a set for faster lookup
mouse_gene_ids = set(mouse_genes["id"].values)

# Vectorized operation for source_id
knowledge_graph["source_id"] = knowledge_graph["source_id"].map(
    lambda x: human_mouse_gene_map.get(x, x) if x in mouse_gene_ids else x
)

# Vectorized operation for target_id
knowledge_graph["target_id"] = knowledge_graph["target_id"].map(
    lambda x: human_mouse_gene_map.get(x, x) if x in mouse_gene_ids else x
)

# Check whether the conversion is successful
mouse_relations = knowledge_graph[
    knowledge_graph["source_id"].isin(mouse_genes["id"])
    | knowledge_graph["target_id"].isin(mouse_genes["id"])
]

human_relations = knowledge_graph[
    knowledge_graph["source_id"].isin(human_genes["id"])
    | knowledge_graph["target_id"].isin(human_genes["id"])
]

# We cannot use the pattern below because some gene names don't follow the pattern. for example, "Bdnf" is used as a human gene in GNBR database.
# pattern = r"^[A-Z][a-z]+$"
# not_matched_genes = knowledge_graph[
#     ((knowledge_graph["source_type"] == "Gene") & knowledge_graph["source_name"].str.match(pattern, na=False)) |
#     ((knowledge_graph["target_type"] == "Gene") & knowledge_graph["target_name"].str.match(pattern, na=False))
# ]
# not_matched_genes[
#     (not_matched_genes["source_id"] == "ENTREZ:627")
#     | (not_matched_genes["target_id"] == "ENTREZ:627")
# ]

print(len(mouse_relations), len(human_relations))
mouse_relations

17284 10083075


relation_type resource  pmids  \
1388      CTD::decreases^expression::Compound:Gene      CTD    NaN   
1389      CTD::decreases^expression::Compound:Gene      CTD    NaN   
1469     CTD::increases^methylation::Compound:Gene      CTD    NaN   
1470       CTD::affects^methylation::Compound:Gene      CTD    NaN   
1471      CTD::decreases^expression::Compound:Gene      CTD    NaN   
...                                            ...      ...    ...   
5823404                      GNBR::L::Gene:Disease     GNBR    NaN   
5823478                      GNBR::J::Gene:Disease     GNBR    NaN   
5823673                      GNBR::L::Gene:Disease     GNBR    NaN   
5823904                      GNBR::L::Gene:Disease     GNBR    NaN   
5823968                      GNBR::L::Gene:Disease     GNBR    NaN   

         key_sentence         source_id source_type         target_id  \
1388              NaN  DrugBank:DB06973    Compound  ENTREZ:100009609   
1389              NaN  DrugBank:DB00158    Compound  ENTREZ:100009609   
1469              NaN  DrugBank:DB06973    Compound     ENTREZ:100012   
1470              NaN      MESH:D001335    Compound     ENTREZ:100012   
1471              NaN      MESH:D004390    Compound     ENTREZ:100012   
...               ...               ...         ...               ...   
5823404           NaN  ENTREZ:101055843        Gene     MONDO:0013209   
5823478           NaN     ENTREZ:387140        Gene     MONDO:0013209   
5823673           NaN      ENTREZ:22060        Gene     MONDO:0006468   
5823904           NaN      ENTREZ:22060        Gene     MONDO:0100460   
5823968           NaN     ENTREZ:387140        Gene     MONDO:0009006   

        target_type        source_name  \
1388           Gene        BISPHENOL A   
1389           Gene         FOLIC ACID   
1469           Gene        BISPHENOL A   
1470           Gene  Vehicle Emissions   
1471           Gene       Chlorpyrifos   
...             ...                ...   
5823404     Disease            Gm12551   
5823478     Disease             Mir21a   
5823673     Disease           Trp53-ps   
5823904     Disease           Trp53-ps   
5823968     Disease             Mir21a   

                                               target_name  \
1388                                               Vmn2r65   
1389                                               Vmn2r65   
1469                                                  Oog3   
1470                                                  Oog3   
1471                                                  Oog3   
...                                                    ...   
5823404  metabolic dysfunction-associated steatotic liv...   
5823478  metabolic dysfunction-associated steatotic liv...   
5823673  thyroid gland undifferentiated (anaplastic) ca...   
5823904               tobacco addiction, susceptibility to   
5823968                  complement component 2 deficiency   

                     formatted_relation_type  
1388            BioMedGPS::E-::Compound:Gene  
1389            BioMedGPS::E-::Compound:Gene  
1469     BioMedGPS::Activator::Compound:Gene  
1470     BioMedGPS::Modulator::Compound:Gene  
1471            BioMedGPS::E-::Compound:Gene  
...                                      ...  
5823404    BioMedGPS::Promotor::Gene:Disease  
5823478      BioMedGPS::Causer::Gene:Disease  
5823673    BioMedGPS::Promotor::Gene:Disease  
5823904    BioMedGPS::Promotor::Gene:Disease  
5823968    BioMedGPS::Promotor::Gene:Disease  

[17284 rows x 11 columns]

In [98]:
len(knowledge_graph)

10549943

### Distribution of Entities in the Graph

In [105]:
from collections import Counter
import pandas as pd

source_entities = knowledge_graph[["source_id", "source_type"]].rename(
    columns={"source_id": "entity_id", "source_type": "entity_type"}
)
target_entities = knowledge_graph[["target_id", "target_type"]]
target_entities.columns = ["entity_id", "entity_type"]
entities = pd.concat([source_entities, target_entities], axis=0).drop_duplicates()
entity_counts = Counter(entities["entity_type"])

entity_df = pd.DataFrame.from_dict(entity_counts, orient="index").reset_index()
entity_df.columns = ["Entity Type", "Count"]

entity_df

Entity Type  Count
0            Compound  24433
1                Gene  32894
2             Disease   9392
3  PharmacologicClass    345
4             Anatomy    513
5   BiologicalProcess  14550
6   CellularComponent   1855
7             Pathway   2310
8   MolecularFunction   4711
9             Symptom    462

In [106]:
import plotly.express as px

fig = px.bar(
    entity_df,
    x="Entity Type",
    y="Count",
    title="Distribution of Entity Types in the Graph",
)

fig.show()

### Distribution of the number of edges of each node

In [108]:
import pandas as pd
import networkx as nx
import math

degree_sequence = dict(G.degree())
node_names = nx.get_node_attributes(G, "name")
degree_data = [
    (f"{n}-{node_names.get(n)}", degree_sequence[n], n[1])
    for n in G.nodes
]

grouped_entity_df = pd.DataFrame(degree_data, columns=["Node Name", "Degree", "Node Type"])
# 找到 Degree 列的最大值
max_degree = grouped_entity_df["Degree"].max()

# 定义 bins 和 labels
step = 100  # 设置每个 bin 的步长
bins = list(range(0, int(math.ceil(max_degree / step)) * step + step, step))
labels = [f"{bins[i]}-{bins[i + 1] - 1}" for i in range(len(bins) - 1)]
labels[-1] = f"{bins[-2]}+"  # 最后一个标签表示最大范围

grouped_entity_df["Category"] = pd.cut(
    grouped_entity_df["Degree"], bins=bins, labels=labels, right=False
)

grouped_entity_df

Node Name  Degree Node Type  \
0      ('MESH:C000611729', 'Compound')-source_name   ...     996  Compound   
1      ('ENTREZ:1', 'Gene')-source_name    A1BG\nsour...     472      Gene   
2      ('MESH:C000944', 'Compound')-source_name    di...    3407  Compound   
3      ('MESH:C005556', 'Compound')-source_name    pr...    2056  Compound   
4      ('MESH:C006253', 'Compound')-source_name    pi...   15645  Compound   
...                                                  ...     ...       ...   
99367  ('MedDRA:10028817', 'Symptom')-target_name    ...       2   Symptom   
99368  ('MedDRA:10041367', 'Symptom')-target_name    ...       2   Symptom   
99369  ('MedDRA:10033386', 'Symptom')-target_name    ...       2   Symptom   
99370  ('MedDRA:10050007', 'Symptom')-target_name    ...       2   Symptom   
99371  ('SYMP:0000551', 'Symptom')-target_name    dis...       2   Symptom   

          Category  
0          900-999  
1          400-499  
2        3400-3499  
3        2000-2099  
4      15600-15699  
...            ...  
99367         0-99  
99368         0-99  
99369         0-99  
99370         0-99  
99371         0-99  

[99372 rows x 4 columns]

In [110]:
import plotly.express as px

fig = px.histogram(
    grouped_entity_df.sort_values("Degree", ascending=False),
    x="Category",
    y="Degree",
    title="Node Degree Distribution",
    category_orders={"Category": labels},
)
fig.show()

In [111]:
import plotly.express as px

fig = px.histogram(
    grouped_entity_df,
    x="Category",
    y="Degree",
    color="Node Type",
    title="Node Degree Distribution by Node Type",
    category_orders={"Category": labels},
    barmode="group",  # 使用分组柱状图
)
fig.show()